# Lab 4: Recurrent models

This lab is supposed to give you some initial practice with neural models in NLP.

**This is the first part of Lab 4.** The purpose of the first part of the lab is to get you started with using neural models. The lab will be updated next week with more exercises.

In the first part of lab 4, we will play with training a recurrent model for part of speech tagging. As an easy exercise, you will observe what happens when you plug in pretrained word embeddings into an neural NLP model and will experiment with different sizes of training data.

## Exercise 1: prepare the data

Linguistic data come in a variety of formats. You already had a chance to play with POS-annotated corpus data in Lab 1.

In the first exercise, you will access POS-annotated data in one format (NLTK) and save it on the disk in a text format. Start with the tagged sentences from the Brown corpus, which can be retrieved as below:

In [1]:
import random
import nltk
#nltk.download('brown')


Now randomize the order of all sentences in the corpus using <code>random.shuffle()</code> function and split it into 50K sentences for training, 5K for validation, and the rest for testing.

In [26]:
sentences = [sent for sent in nltk.corpus.brown.tagged_sents()]
print(type(sentences))
shuffled_sentences = random.sample(sentences, len(sentences))
type(shuffled_sentences)

training_brown= shuffled_sentences[:49999]
validation_brown=shuffled_sentences[50000:54999]
testing_brown= shuffled_sentences[55000:]

<class 'list'>


Define a function for saving your datasets to a text file in the following format:
* one sentence per line
* tokens separated by spaces
* POS tag separated from the token by "###", for example <code>said###VBD</code>.

In [41]:
def write_posdata(sentences,outfile):
    storage = ""
    for sent in sentences:
        phrase = ""
        for i in sent:
            phrase = phrase + (i[0]+"###"+i[1]+" ")
        phrase = phrase +"\n"
        storage = storage + phrase
    file = open(outfile,"w") 
    file.write(storage)
    file.close() 
    

Now save your data partitions in different sizes. We will start with small data samples since training on a large dataset may be very slow depending on your machine.

In [42]:
write_posdata(training_brown,"train_brown.txt")
write_posdata(testing_brown,"test_brown.txt")
write_posdata(validation_brown,"validation_brown.txt")
write_posdata(training_brown[:50],"train_brown_50.txt")
write_posdata(validation_brown[:50],"validation_brown_50.txt")
write_posdata(training_brown[:500],"train_brown_500.txt")
write_posdata(validation_brown[:500],"validation_brown_500.txt")
write_posdata(training_brown[:5000],"train_brown_5000.txt")

Congratulations, you have now saved the POS tagged data for model training purposes!

## Exercise 2: train neural POS tagger models

We will now play with a neural model. First of all, install <code>allennlp</code>. The LSTM model we will train follows the AllenNLP tutorial https://allennlp.org/tutorials which contains ample explanations of the underlying code. Let us start by loading the model code and data, starting with a tiny sample for demonstration purposes

In [2]:
from lstm_tutorial import *

train_dataset_tiny = reader.read("train_brown_50.txt")
validation_dataset_tiny = reader.read("validation_brown_50.txt")

50it [00:00, 1087.16it/s]
50it [00:00, 1189.62it/s]


Fist of all we need to initialize the vocabulary and define an embedding (vector) for each token. We set the embedding size at 300, common in realistic applications. By default, the embeddings are initialized randomly and updated during trining (this can be changed but we start with a standard configuration). We also need to specify the <code>HIDDEN_DIM</code> parameter: the dimensionality of the hidden vector representations in the LSTM cell.

In [3]:
vocab_tiny = Vocabulary.from_instances(train_dataset_tiny + validation_dataset_tiny)

EMBEDDING_DIM = 300
HIDDEN_DIM = 20

token_embedding_tiny = Embedding(num_embeddings=vocab_tiny.get_vocab_size('tokens'),
                            embedding_dim=EMBEDDING_DIM)

100%|█████████████████████████████████████████████████████████████████████████████| 100/100 [00:00<00:00, 25001.81it/s]


Download the smallest pretrained word vector model from https://nlp.stanford.edu/projects/glove/, unzip it, and extract the relevant file <code>'glove.6B.300d.txt'</code> in your working directory.

In [5]:
glove_token_embedding_tiny = Embedding.from_params(vocab=vocab_tiny,
                            params=Params({'pretrained_file':'glove.6B.300d.txt',
                                           'embedding_dim' : EMBEDDING_DIM}))

400000it [00:06, 64840.04it/s]


Now from embedding a single word with <code>token_embedding_tiny</code> we can proceed to mapping a word sequence into a sequence of vectors:

In [6]:
word_embeddings_tiny = BasicTextFieldEmbedder({"tokens": token_embedding_tiny})

The following initializes parameters of an LSTM model using <code>word_embeddings_tiny</code> input encoding

In [7]:
lstm = PytorchSeq2SeqWrapper(torch.nn.LSTM(EMBEDDING_DIM, HIDDEN_DIM, batch_first=True))

model_tiny = LstmTagger(word_embeddings_tiny, lstm, vocab_tiny)

Now define an LSTM model called <code>glove_model_tiny</code> that uses <code>glove_token_embedding_tiny</code>:

In [20]:
glove_word_embeddings_tiny = BasicTextFieldEmbedder({"tokens": glove_token_embedding_tiny})
glove_model_tiny = LstmTagger(glove_word_embeddings_tiny, lstm, vocab_tiny)

Train the basic model for the tiny dataset:

In [9]:
basic_trainer_tiny=initialize_trainer(model_tiny,vocab_tiny,train_dataset_tiny,validation_dataset_tiny,batch_size=50)
basic_trainer_tiny.train()

accuracy: 0.0773, loss: 4.4504 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:02<00:00,  2.00s/it]
accuracy: 0.0771, loss: 4.4565 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 17.55it/s]
accuracy: 0.0782, loss: 4.4451 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.03it/s]
accuracy: 0.0800, loss: 4.4513 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.52it/s]
accuracy: 0.0801, loss: 4.4397 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.33it/s]
accuracy: 0.0850, loss: 4.4462 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.52it/s]
accuracy: 0.0858, loss: 4.4344 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.29it/s]
accuracy: 0.0850, loss: 4.4410 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.52it/s]
accuracy: 0.0858, loss: 4.4291 ||: 100%|

accuracy: 0.1583, loss: 4.0742 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.54it/s]
accuracy: 0.1403, loss: 4.0918 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.41it/s]
accuracy: 0.1583, loss: 4.0682 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.68it/s]
accuracy: 0.1403, loss: 4.0860 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 16.13it/s]
accuracy: 0.1583, loss: 4.0622 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.24it/s]
accuracy: 0.1403, loss: 4.0802 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 16.39it/s]
accuracy: 0.1583, loss: 4.0561 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.80it/s]
accuracy: 0.1403, loss: 4.0744 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.41it/s]
accuracy: 0.1583, loss: 4.0501 ||: 100%|

accuracy: 0.1583, loss: 3.7375 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.95it/s]
accuracy: 0.1403, loss: 3.7671 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.18it/s]
accuracy: 0.1583, loss: 3.7345 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.67it/s]
accuracy: 0.1403, loss: 3.7641 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.00it/s]
accuracy: 0.1583, loss: 3.7315 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.90it/s]
accuracy: 0.1403, loss: 3.7611 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.87it/s]
accuracy: 0.1583, loss: 3.7285 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.80it/s]
accuracy: 0.1403, loss: 3.7582 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.87it/s]
accuracy: 0.1583, loss: 3.7257 ||: 100%|

accuracy: 0.1583, loss: 3.6065 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.68it/s]
accuracy: 0.1403, loss: 3.6291 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.18it/s]
accuracy: 0.1583, loss: 3.6053 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.38it/s]
accuracy: 0.1403, loss: 3.6278 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.87it/s]
accuracy: 0.1583, loss: 3.6041 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.18it/s]
accuracy: 0.1403, loss: 3.6264 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.87it/s]
accuracy: 0.1583, loss: 3.6029 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.75it/s]
accuracy: 0.1403, loss: 3.6251 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 16.67it/s]
accuracy: 0.1583, loss: 3.6018 ||: 100%|

accuracy: 0.1583, loss: 3.5459 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.58it/s]
accuracy: 0.1403, loss: 3.5612 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.87it/s]
accuracy: 0.1583, loss: 3.5453 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.90it/s]
accuracy: 0.1403, loss: 3.5604 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.00it/s]
accuracy: 0.1583, loss: 3.5446 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.37it/s]
accuracy: 0.1403, loss: 3.5597 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 17.86it/s]
accuracy: 0.1583, loss: 3.5439 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.85it/s]
accuracy: 0.1403, loss: 3.5590 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 16.95it/s]
accuracy: 0.1583, loss: 3.5433 ||: 100%|

...

accuracy: 0.3110, loss: 3.1752 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.85it/s]
accuracy: 0.2836, loss: 3.2188 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 21.28it/s]
accuracy: 0.3120, loss: 3.1739 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.58it/s]
accuracy: 0.2826, loss: 3.2176 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 14.29it/s]
accuracy: 0.3120, loss: 3.1725 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  4.61it/s]
accuracy: 0.2836, loss: 3.2163 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 17.86it/s]
accuracy: 0.3139, loss: 3.1711 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.29it/s]
accuracy: 0.2846, loss: 3.2151 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 22.73it/s]
accuracy: 0.3139, loss: 3.1698 ||: 100%|

accuracy: 0.3544, loss: 3.0820 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  2.82it/s]
accuracy: 0.3330, loss: 3.1359 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 14.29it/s]
accuracy: 0.3553, loss: 3.0806 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  3.16it/s]
accuracy: 0.3360, loss: 3.1347 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 12.99it/s]
accuracy: 0.3553, loss: 3.0792 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  4.29it/s]
accuracy: 0.3370, loss: 3.1335 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 19.61it/s]
accuracy: 0.3563, loss: 3.0779 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  3.86it/s]
accuracy: 0.3389, loss: 3.1323 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 15.39it/s]
accuracy: 0.3591, loss: 3.0765 ||: 100%|

accuracy: 0.3874, loss: 2.9894 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  4.95it/s]
accuracy: 0.3755, loss: 3.0548 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.19it/s]
accuracy: 0.3883, loss: 2.9881 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.85it/s]
accuracy: 0.3765, loss: 3.0536 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.84it/s]
accuracy: 0.3883, loss: 2.9867 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.21it/s]
accuracy: 0.3765, loss: 3.0524 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.00it/s]
accuracy: 0.3893, loss: 2.9853 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.14it/s]
accuracy: 0.3765, loss: 3.0512 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.41it/s]
accuracy: 0.3911, loss: 2.9840 ||: 100%|

accuracy: 0.4138, loss: 2.8964 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.21it/s]
accuracy: 0.3854, loss: 2.9750 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 23.26it/s]
accuracy: 0.4138, loss: 2.8950 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  2.98it/s]
accuracy: 0.3854, loss: 2.9738 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 11.91it/s]
accuracy: 0.4138, loss: 2.8936 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  3.04it/s]
accuracy: 0.3854, loss: 2.9726 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.87it/s]
accuracy: 0.4138, loss: 2.8922 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  3.18it/s]
accuracy: 0.3854, loss: 2.9715 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 12.35it/s]
accuracy: 0.4147, loss: 2.8909 ||: 100%|

{'best_epoch': 999,
 'peak_cpu_memory_MB': 0,
 'training_duration': '0:03:52.203449',
 'training_start_epoch': 0,
 'training_epochs': 999,
 'epoch': 999,
 'training_accuracy': 0.4213006597549482,
 'training_loss': 2.831315279006958,
 'training_cpu_memory_MB': 0.0,
 'validation_accuracy': 0.40217391304347827,
 'validation_loss': 2.9210851192474365,
 'best_validation_accuracy': 0.40217391304347827,
 'best_validation_loss': 2.9210851192474365}

You have trained an LSTM POS tagger for the basic model. Now train the <code>glove_model_tiny</code>. 

In [21]:
trainer_glove_model_tiny=initialize_trainer(glove_model_tiny,vocab_tiny,train_dataset_tiny,validation_dataset_tiny,batch_size=50)
trainer_glove_model_tiny.train()

accuracy: 0.0113, loss: 4.5604 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.03it/s]
accuracy: 0.0079, loss: 4.5485 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 16.40it/s]
accuracy: 0.0113, loss: 4.5390 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.81it/s]
accuracy: 0.0089, loss: 4.5287 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 16.95it/s]
accuracy: 0.0113, loss: 4.5189 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.68it/s]
accuracy: 0.0119, loss: 4.5100 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 16.67it/s]
accuracy: 0.0141, loss: 4.4998 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.21it/s]
accuracy: 0.0138, loss: 4.4923 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.52it/s]
accuracy: 0.0179, loss: 4.4817 ||: 100%|

accuracy: 0.1649, loss: 3.6746 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.62it/s]
accuracy: 0.1472, loss: 3.7050 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 21.28it/s]
accuracy: 0.1659, loss: 3.6688 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  7.75it/s]
accuracy: 0.1472, loss: 3.6993 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 21.28it/s]
accuracy: 0.1668, loss: 3.6632 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.71it/s]
accuracy: 0.1492, loss: 3.6938 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 22.23it/s]
accuracy: 0.1668, loss: 3.6577 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.95it/s]
accuracy: 0.1502, loss: 3.6883 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.87it/s]
accuracy: 0.1678, loss: 3.6523 ||: 100%|

accuracy: 0.2074, loss: 3.4230 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  7.20it/s]
accuracy: 0.1808, loss: 3.4583 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 21.28it/s]
accuracy: 0.2064, loss: 3.4202 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.67it/s]
accuracy: 0.1818, loss: 3.4558 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 21.28it/s]
accuracy: 0.2064, loss: 3.4175 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.25it/s]
accuracy: 0.1818, loss: 3.4533 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 19.23it/s]
accuracy: 0.2064, loss: 3.4147 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.41it/s]
accuracy: 0.1818, loss: 3.4507 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.84it/s]
accuracy: 0.2074, loss: 3.4120 ||: 100%|

accuracy: 0.2234, loss: 3.2416 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.85it/s]
accuracy: 0.1877, loss: 3.3011 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 21.74it/s]
accuracy: 0.2253, loss: 3.2389 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.14it/s]
accuracy: 0.1877, loss: 3.2989 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.41it/s]
accuracy: 0.2253, loss: 3.2362 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.21it/s]
accuracy: 0.1877, loss: 3.2966 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.41it/s]
accuracy: 0.2262, loss: 3.2335 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.47it/s]
accuracy: 0.1887, loss: 3.2944 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.84it/s]
accuracy: 0.2271, loss: 3.2308 ||: 100%|

accuracy: 0.2479, loss: 3.0528 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  7.30it/s]
accuracy: 0.2045, loss: 3.1459 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 22.73it/s]
accuracy: 0.2479, loss: 3.0500 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  7.30it/s]
accuracy: 0.2055, loss: 3.1436 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 25.65it/s]
accuracy: 0.2479, loss: 3.0473 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.99it/s]
accuracy: 0.2055, loss: 3.1413 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 22.73it/s]
accuracy: 0.2479, loss: 3.0445 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  7.41it/s]
accuracy: 0.2055, loss: 3.1391 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.84it/s]
accuracy: 0.2488, loss: 3.0418 ||: 100%|

...

accuracy: 0.5768, loss: 1.9689 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  7.14it/s]
accuracy: 0.4872, loss: 2.3390 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.84it/s]
accuracy: 0.5768, loss: 1.9673 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.95it/s]
accuracy: 0.4881, loss: 2.3381 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.41it/s]
accuracy: 0.5768, loss: 1.9658 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.41it/s]
accuracy: 0.4901, loss: 2.3371 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.41it/s]
accuracy: 0.5778, loss: 1.9642 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.37it/s]
accuracy: 0.4911, loss: 2.3361 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 23.26it/s]
accuracy: 0.5796, loss: 1.9626 ||: 100%|

accuracy: 0.6032, loss: 1.8648 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  7.09it/s]
accuracy: 0.5119, loss: 2.2764 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.00it/s]
accuracy: 0.6032, loss: 1.8633 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.85it/s]
accuracy: 0.5119, loss: 2.2756 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 21.28it/s]
accuracy: 0.6051, loss: 1.8619 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  7.04it/s]
accuracy: 0.5119, loss: 2.2747 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.41it/s]
accuracy: 0.6051, loss: 1.8604 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.33it/s]
accuracy: 0.5119, loss: 2.2739 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 17.55it/s]
accuracy: 0.6060, loss: 1.8589 ||: 100%|

accuracy: 0.6249, loss: 1.7676 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.71it/s]
accuracy: 0.5198, loss: 2.2211 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 17.86it/s]
accuracy: 0.6249, loss: 1.7662 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  7.14it/s]
accuracy: 0.5198, loss: 2.2203 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.00it/s]
accuracy: 0.6249, loss: 1.7648 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.76it/s]
accuracy: 0.5198, loss: 2.2195 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 22.23it/s]
accuracy: 0.6249, loss: 1.7634 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  7.20it/s]
accuracy: 0.5198, loss: 2.2188 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.00it/s]
accuracy: 0.6249, loss: 1.7620 ||: 100%|

accuracy: 0.6390, loss: 1.6766 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  7.04it/s]
accuracy: 0.5336, loss: 2.1705 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 22.23it/s]
accuracy: 0.6390, loss: 1.6753 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.95it/s]
accuracy: 0.5346, loss: 2.1698 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 24.39it/s]
accuracy: 0.6390, loss: 1.6741 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  7.25it/s]
accuracy: 0.5346, loss: 2.1691 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.41it/s]
accuracy: 0.6390, loss: 1.6728 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.49it/s]
accuracy: 0.5346, loss: 2.1685 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.84it/s]
accuracy: 0.6390, loss: 1.6716 ||: 100%|

{'best_epoch': 999,
 'peak_cpu_memory_MB': 0,
 'training_duration': '0:03:30.964794',
 'training_start_epoch': 0,
 'training_epochs': 999,
 'epoch': 999,
 'training_accuracy': 0.6503298774740811,
 'training_loss': 1.6193351745605469,
 'training_cpu_memory_MB': 0.0,
 'validation_accuracy': 0.5355731225296443,
 'validation_loss': 2.1408300399780273,
 'best_validation_accuracy': 0.5355731225296443,
 'best_validation_loss': 2.1408300399780273}

## Exercise 3: Explore training parameters

Create separate models on the basis of bigger datasets: the 500 sentence training and 500 sentence validation and 5000 sentence training and 5000 sentence validation. Using the full training set (50K sentences) is optional (your machine might be too slow). Initialize and train the basic model on 500 sentence training and 500 sentence validation data:

In [25]:
#train the basic model on 500 sentences
train_dataset_regular= reader.read("train_brown_500.txt")
validation_dataset_regular = reader.read("validation_brown_500.txt")

vocab_regular = Vocabulary.from_instances(train_dataset_regular + validation_dataset_regular)

EMBEDDING_DIM = 300
HIDDEN_DIM = 20

token_embedding_regular = Embedding(num_embeddings=vocab_regular.get_vocab_size('tokens'),
                            embedding_dim=EMBEDDING_DIM)

word_embeddings_regular = BasicTextFieldEmbedder({"tokens": token_embedding_regular})

lstm = PytorchSeq2SeqWrapper(torch.nn.LSTM(EMBEDDING_DIM, HIDDEN_DIM, batch_first=True))

model_regular = LstmTagger(word_embeddings_regular, lstm, vocab_regular)

basic_trainer_regular=initialize_trainer(model_regular,vocab_regular,train_dataset_regular,validation_dataset_regular,batch_size=50)
basic_trainer_regular.train()



500it [00:00, 9259.56it/s]


500it [00:00, 6411.19it/s]


100%|███████████████████████████████████████████████████████████████████████████| 1000/1000 [00:00<00:00, 19232.78it/s]


  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
                                                                                                                    

  0%|                                                                                           | 0/10 [03:48<?, ?it/s]

accuracy: 0.0000, loss: 5.2316 ||:  10%|████▊                                           | 1/10 [00:00<00:02,  3.53it/s]
accuracy: 0.0003, loss: 5.2269 ||:  30%|██████████████▍                                 | 3/10 [00:00<00:01,  4.30it/s]
accuracy: 0.0004, loss: 5.2246 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:01,  3.98it/s]
accuracy: 0.0005, loss: 5.2158 ||:  60%|████████████████████████████▊                   | 6/10 [00:

accuracy: 0.1345, loss: 4.2163 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00,  8.42it/s]
accuracy: 0.1342, loss: 4.2129 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00,  8.25it/s]
accuracy: 0.1349, loss: 4.2013 ||:  70%|█████████████████████████████████▌              | 7/10 [00:01<00:00,  5.45it/s]
accuracy: 0.1293, loss: 4.2593 ||: 100%|███████████████████████████████████████████████| 10/10 [00:01<00:00,  8.69it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.1203, loss: 4.2467 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 52.64it/s]
accuracy: 0.1360, loss: 4.1811 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 35.72it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.1161, loss: 4.1895 ||:  20

accuracy: 0.1298, loss: 3.8243 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 12.25it/s]
accuracy: 0.1296, loss: 3.8101 ||:  70%|█████████████████████████████████▌              | 7/10 [00:00<00:00, 11.24it/s]
accuracy: 0.1293, loss: 3.8075 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 10.80it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.1217, loss: 3.8404 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 56.08it/s]
accuracy: 0.1360, loss: 3.7533 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 35.72it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.1138, loss: 3.7344 ||:  20%|█████████▌                                      | 2/10 [00:00<00:00, 16.26it/s]
accuracy: 0.1262, loss: 3.7252 ||:  30

accuracy: 0.1293, loss: 3.7060 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 11.00it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.1223, loss: 3.7369 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 48.39it/s]
accuracy: 0.1360, loss: 3.6555 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 31.55it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.1179, loss: 3.6037 ||:  10%|████▊                                           | 1/10 [00:00<00:00,  9.18it/s]
accuracy: 0.1254, loss: 3.5854 ||:  30%|██████████████▍                                 | 3/10 [00:00<00:00,  8.17it/s]
accuracy: 0.1278, loss: 3.5925 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:00,  8.41it/s]
accuracy: 0.1264, loss: 3.7247 ||:  60

accuracy: 0.1615, loss: 3.6491 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 11.21it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.1880, loss: 3.6778 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 52.18it/s]
accuracy: 0.1779, loss: 3.5989 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 33.45it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.1790, loss: 3.4491 ||:  10%|████▊                                           | 1/10 [00:00<00:01,  7.04it/s]
accuracy: 0.1617, loss: 3.5647 ||:  30%|██████████████▍                                 | 3/10 [00:00<00:00,  8.32it/s]
accuracy: 0.1688, loss: 3.6179 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 10.07it/s]
accuracy: 0.1703, loss: 3.6974 ||:  70

...

accuracy: 0.8838, loss: 0.6506 ||: 100%|███████████████████████████████████████████████| 10/10 [00:01<00:00,  9.82it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.7050, loss: 1.4851 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 49.03it/s]
accuracy: 0.6944, loss: 1.3632 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 32.26it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.8953, loss: 0.5864 ||:  10%|████▊                                           | 1/10 [00:00<00:01,  6.25it/s]
accuracy: 0.8909, loss: 0.6173 ||:  30%|██████████████▍                                 | 3/10 [00:00<00:01,  6.94it/s]
accuracy: 0.8888, loss: 0.6357 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00,  8.00it/s]
accuracy: 0.8852, loss: 0.6291 ||:  70

accuracy: 0.8842, loss: 0.6454 ||:  10%|████▊                                           | 1/10 [00:00<00:00,  9.62it/s]
accuracy: 0.8784, loss: 0.6497 ||:  20%|█████████▌                                      | 2/10 [00:00<00:01,  6.17it/s]
accuracy: 0.8854, loss: 0.6268 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:00,  7.48it/s]
accuracy: 0.8895, loss: 0.6123 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00,  7.20it/s]
accuracy: 0.8902, loss: 0.6238 ||:  80%|██████████████████████████████████████▍         | 8/10 [00:00<00:00,  8.71it/s]
accuracy: 0.8877, loss: 0.6369 ||: 100%|███████████████████████████████████████████████| 10/10 [00:01<00:00,  9.24it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.7040, loss: 1.4848 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 48.08it/s]
accuracy: 0.6969, loss: 1.3580 ||: 100%

accuracy: 0.8958, loss: 0.6169 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:00, 10.39it/s]
accuracy: 0.8884, loss: 0.6228 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00,  6.62it/s]
accuracy: 0.8901, loss: 0.6150 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00,  7.25it/s]
accuracy: 0.8888, loss: 0.6244 ||: 100%|███████████████████████████████████████████████| 10/10 [00:01<00:00,  9.55it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.7051, loss: 1.4442 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 47.63it/s]
accuracy: 0.6980, loss: 1.3551 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 31.16it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.8835, loss: 0.6881 ||:  30

accuracy: 0.7088, loss: 1.4728 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 45.46it/s]
accuracy: 0.6989, loss: 1.3525 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 30.96it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.8900, loss: 0.6439 ||:  20%|█████████▌                                      | 2/10 [00:00<00:00, 15.39it/s]
accuracy: 0.8929, loss: 0.6083 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:00, 15.32it/s]
accuracy: 0.8908, loss: 0.6190 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 11.89it/s]
accuracy: 0.8870, loss: 0.6177 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00,  6.91it/s]
accuracy: 0.8906, loss: 0.6085 ||:  80%|██████████████████████████████████████▍         | 8/10 [00:00<00:00,  7.96it/s]
accuracy: 0.8914, loss: 0.6116 ||: 100%

{'best_epoch': 994,
 'peak_cpu_memory_MB': 0,
 'training_duration': '0:21:10.950190',
 'training_start_epoch': 0,
 'training_epochs': 999,
 'epoch': 999,
 'training_accuracy': 0.8920169687620517,
 'training_loss': 0.6088885605335236,
 'training_cpu_memory_MB': 0.0,
 'validation_accuracy': 0.6997991967871486,
 'validation_loss': 1.3516964554786681,
 'best_validation_accuracy': 0.6991967871485943,
 'best_validation_loss': 1.3496984839439392}

Now do the same training (500 sentence training and 500 sentence validation sets) with GloVE embeddings:

In [26]:
glove_token_embedding_regular = Embedding.from_params(vocab=vocab_regular,
                            params=Params({'pretrained_file':'glove.6B.300d.txt',
                                           'embedding_dim' : EMBEDDING_DIM}))

glove_word_embeddings_regular = BasicTextFieldEmbedder({"tokens": glove_token_embedding_regular})
glove_model_regular = LstmTagger(glove_word_embeddings_regular, lstm, vocab_regular)

trainer_glove_model_regular=initialize_trainer(glove_model_regular,vocab_regular,train_dataset_regular,validation_dataset_regular,batch_size=50)
trainer_glove_model_regular.train()


0it [00:00, ?it/s]
279it [00:00, 2762.84it/s]
912it [00:00, 3319.81it/s]
1731it [00:00, 4034.76it/s]
2984it [00:00, 5058.86it/s]
4678it [00:00, 6399.88it/s]
6845it [00:00, 8106.49it/s]
9818it [00:00, 10358.36it/s]
12713it [00:00, 12813.47it/s]
17165it [00:00, 16277.40it/s]
21335it [00:01, 19892.81it/s]
26254it [00:01, 24185.28it/s]
32041it [00:01, 29258.33it/s]
37586it [00:01, 34027.01it/s]
42503it [00:01, 37406.75it/s]
47383it [00:01, 40125.68it/s]
52375it [00:01, 42528.84it/s]
57198it [00:01, 43973.81it/s]
62173it [00:01, 45437.96it/s]
67085it [00:01, 46353.74it/s]
72175it [00:02, 47498.78it/s]
77081it [00:02, 47678.67it/s]
82179it [00:02, 48487.28it/s]
87108it [00:02, 48440.25it/s]
92008it [00:02, 39452.27it/s]
96264it [00:02, 38060.08it/s]
101124it [00:02, 40613.31it/s]
106235it [00:02, 43172.14it/s]
111100it [00:02, 44560.38it/s]
116072it [00:03, 45867.11it/s]
120769it [00:03, 37642.50it/s]
125420it [00:03, 39826.48it/s]
130025it [00:03, 41399.38it/s]
134723it [00:03, 42695.54it/

accuracy: 0.2624, loss: 3.6988 ||:  90%|███████████████████████████████████████████▏    | 9/10 [00:00<00:00,  8.82it/s]
accuracy: 0.2665, loss: 3.6787 ||: 100%|███████████████████████████████████████████████| 10/10 [00:01<00:00,  9.21it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.2846, loss: 3.7341 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 43.11it/s]
accuracy: 0.2906, loss: 3.6405 ||:  80%|██████████████████████████████████████▍         | 8/10 [00:00<00:00, 37.83it/s]
accuracy: 0.2904, loss: 3.6018 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 29.50it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.2909, loss: 3.5281 ||:  20%|█████████▌                                      | 2/10 [00:00<00:00,  8.27it/s]
accuracy: 0.2844, loss: 3.6025 ||:  40

accuracy: 0.3601, loss: 3.2173 ||: 100%|███████████████████████████████████████████████| 10/10 [00:01<00:00,  9.28it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.3469, loss: 3.2666 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 47.25it/s]
accuracy: 0.3645, loss: 3.1523 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 31.45it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.3506, loss: 3.2551 ||:  20%|█████████▌                                      | 2/10 [00:00<00:00, 12.58it/s]
accuracy: 0.3492, loss: 3.1680 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:00, 12.39it/s]
accuracy: 0.3521, loss: 3.1557 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 10.28it/s]
accuracy: 0.3572, loss: 3.1318 ||:  60

accuracy: 0.3837, loss: 3.0157 ||:  70%|█████████████████████████████████▌              | 7/10 [00:00<00:00, 12.84it/s]
accuracy: 0.3985, loss: 2.9674 ||:  80%|██████████████████████████████████████▍         | 8/10 [00:00<00:00,  9.96it/s]
accuracy: 0.4033, loss: 2.9343 ||: 100%|███████████████████████████████████████████████| 10/10 [00:01<00:00,  9.62it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.3806, loss: 3.0357 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 49.03it/s]
accuracy: 0.4101, loss: 2.8777 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 31.35it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.4126, loss: 2.8410 ||:  10%|████▊                                           | 1/10 [00:00<00:01,  7.69it/s]
accuracy: 0.3971, loss: 3.1341 ||:  30

accuracy: 0.4224, loss: 2.7552 ||:  90%|███████████████████████████████████████████▏    | 9/10 [00:00<00:00, 11.35it/s]
accuracy: 0.4243, loss: 2.7351 ||: 100%|███████████████████████████████████████████████| 10/10 [00:01<00:00,  9.29it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.4106, loss: 2.8456 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 45.88it/s]
accuracy: 0.4321, loss: 2.6891 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 31.83it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.4286, loss: 2.5929 ||:  20%|█████████▌                                      | 2/10 [00:00<00:00,  9.18it/s]
accuracy: 0.4389, loss: 2.5809 ||:  30%|██████████████▍                                 | 3/10 [00:00<00:00,  8.11it/s]
accuracy: 0.4266, loss: 2.7739 ||:  60

...

accuracy: 0.9178, loss: 0.4204 ||:  20%|█████████▌                                      | 2/10 [00:00<00:00, 14.71it/s]
accuracy: 0.8867, loss: 0.4656 ||:  30%|██████████████▍                                 | 3/10 [00:00<00:00,  8.02it/s]
accuracy: 0.8860, loss: 0.4739 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00,  9.20it/s]
accuracy: 0.8890, loss: 0.4723 ||:  80%|██████████████████████████████████████▍         | 8/10 [00:00<00:00, 10.65it/s]
accuracy: 0.8877, loss: 0.4918 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 10.85it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.7572, loss: 1.2610 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 58.26it/s]
accuracy: 0.7700, loss: 1.1289 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 36.37it/s]

  0%|                                 

accuracy: 0.8895, loss: 0.4843 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 10.97it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.7587, loss: 1.2636 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 49.19it/s]
accuracy: 0.7710, loss: 1.1277 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 34.61it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.9102, loss: 0.4339 ||:  20%|█████████▌                                      | 2/10 [00:00<00:00, 16.95it/s]
accuracy: 0.9029, loss: 0.4600 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:00, 17.26it/s]
accuracy: 0.8893, loss: 0.4745 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 10.64it/s]
accuracy: 0.8936, loss: 0.4614 ||:  80

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.8674, loss: 0.6495 ||:  10%|████▊                                           | 1/10 [00:00<00:01,  8.70it/s]
accuracy: 0.8841, loss: 0.5562 ||:  20%|█████████▌                                      | 2/10 [00:00<00:00,  8.12it/s]
accuracy: 0.8883, loss: 0.5144 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:00,  9.31it/s]
accuracy: 0.8875, loss: 0.4807 ||:  70%|█████████████████████████████████▌              | 7/10 [00:00<00:00,  9.24it/s]
accuracy: 0.8912, loss: 0.4765 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 10.56it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.7605, loss: 1.2546 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 52.64it/s]
accuracy: 0.7715, loss: 1.1261 ||: 100%

accuracy: 0.7724, loss: 1.1246 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 30.56it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.8716, loss: 0.5398 ||:  10%|████▊                                           | 1/10 [00:00<00:02,  3.92it/s]
accuracy: 0.8790, loss: 0.5390 ||:  30%|██████████████▍                                 | 3/10 [00:00<00:01,  4.81it/s]
accuracy: 0.8867, loss: 0.4802 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00,  6.13it/s]
accuracy: 0.8895, loss: 0.4787 ||:  70%|█████████████████████████████████▌              | 7/10 [00:00<00:00,  6.30it/s]
accuracy: 0.8928, loss: 0.4694 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 10.32it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.7566, loss: 1.3247 ||:  50

{'best_epoch': 998,
 'peak_cpu_memory_MB': 0,
 'training_duration': '0:23:07.505913',
 'training_start_epoch': 0,
 'training_epochs': 999,
 'epoch': 999,
 'training_accuracy': 0.8928846895487852,
 'training_loss': 0.46843344569206236,
 'training_cpu_memory_MB': 0.0,
 'validation_accuracy': 0.772289156626506,
 'validation_loss': 1.1245891630649567,
 'best_validation_accuracy': 0.7725903614457831,
 'best_validation_loss': 1.1243623316287994}

Use a bigger training set now with 5K sentence training and 5K sentence validation sets and random initial embeddings:

In [28]:
train_dataset_big= reader.read("train_brown_5000.txt")
validation_dataset_big = reader.read("validation_brown_500.txt")

vocab_big = Vocabulary.from_instances(train_dataset_big + validation_dataset_big)

EMBEDDING_DIM = 300
HIDDEN_DIM = 20

token_embedding_big = Embedding(num_embeddings=vocab_big.get_vocab_size('tokens'),
                            embedding_dim=EMBEDDING_DIM)

word_embeddings_big = BasicTextFieldEmbedder({"tokens": token_embedding_big})

lstm = PytorchSeq2SeqWrapper(torch.nn.LSTM(EMBEDDING_DIM, HIDDEN_DIM, batch_first=True))

model_big = LstmTagger(word_embeddings_big, lstm, vocab_big)

basic_trainer_big=initialize_trainer(model_big,vocab_big,train_dataset_big,validation_dataset_big,batch_size=50)
basic_trainer_big.train()



0it [00:00, ?it/s]

793it [00:00, 7852.89it/s]
               

  0%|                                                                                         | 0/10 [1:11:30<?, ?it/s]

1029it [00:00, 2570.08it/s]
1808it [00:00, 3212.80it/s]
2926it [00:00, 4082.03it/s]
3928it [00:00, 4950.07it/s]
5000it [00:00, 5483.31it/s]

500it [00:00, 10205.62it/s]

100%|███████████████████████████████████████████████████████████████████████████| 5500/5500 [00:00<00:00, 31071.85it/s]

  0%|                                                                                          | 0/100 [00:00<?, ?it/s]
accuracy: 0.0000, loss: 5.5902 ||:   1%|▍                                              | 1/100 [00:00<00:43,  2.28it/s]
accuracy: 0.0000, loss: 5.5892 ||:   3%|█▍                                             | 3/100 [00:00<00:32,  2.99it/s]
accuracy: 0.0000, loss: 5.5804 ||:   4%|█▉                                             | 4/100 [00:00<00:26,  3.61it/s]
accuracy: 0.0000, loss: 5.5758 ||:   5%|██

accuracy: 0.1312, loss: 4.4370 ||:  86%|███████████████████████████████████████▌      | 86/100 [00:10<00:02,  6.72it/s]
accuracy: 0.1312, loss: 4.4317 ||:  87%|████████████████████████████████████████      | 87/100 [00:10<00:02,  6.12it/s]
accuracy: 0.1312, loss: 4.4280 ||:  88%|████████████████████████████████████████▍     | 88/100 [00:10<00:01,  6.65it/s]
accuracy: 0.1311, loss: 4.4196 ||:  90%|█████████████████████████████████████████▍    | 90/100 [00:11<00:01,  7.32it/s]
accuracy: 0.1309, loss: 4.4198 ||:  92%|██████████████████████████████████████████▎   | 92/100 [00:11<00:00,  8.63it/s]
accuracy: 0.1310, loss: 4.4108 ||:  94%|███████████████████████████████████████████▏  | 94/100 [00:11<00:00,  7.77it/s]
accuracy: 0.1309, loss: 4.4204 ||:  97%|████████████████████████████████████████████▌ | 97/100 [00:11<00:00,  8.82it/s]
accuracy: 0.1307, loss: 4.4112 ||: 100%|█████████████████████████████████████████████| 100/100 [00:12<00:00,  8.25it/s]

  0%|                                  

accuracy: 0.1404, loss: 3.8073 ||:  90%|█████████████████████████████████████████▍    | 90/100 [00:10<00:01,  7.07it/s]
accuracy: 0.1403, loss: 3.8062 ||:  91%|█████████████████████████████████████████▊    | 91/100 [00:10<00:01,  7.48it/s]
accuracy: 0.1402, loss: 3.8043 ||:  92%|██████████████████████████████████████████▎   | 92/100 [00:10<00:01,  7.73it/s]
accuracy: 0.1401, loss: 3.8002 ||:  94%|███████████████████████████████████████████▏  | 94/100 [00:10<00:00,  8.07it/s]
accuracy: 0.1398, loss: 3.7999 ||:  96%|████████████████████████████████████████████▏ | 96/100 [00:11<00:00,  9.20it/s]
accuracy: 0.1397, loss: 3.7987 ||:  97%|████████████████████████████████████████████▌ | 97/100 [00:11<00:00,  9.19it/s]
accuracy: 0.1396, loss: 3.7971 ||:  98%|█████████████████████████████████████████████ | 98/100 [00:11<00:00,  8.97it/s]
accuracy: 0.1394, loss: 3.7965 ||: 100%|█████████████████████████████████████████████| 100/100 [00:11<00:00,  8.72it/s]

  0%|                                  

accuracy: 0.1995, loss: 3.5876 ||:  97%|████████████████████████████████████████████▌ | 97/100 [00:10<00:00,  8.14it/s]
accuracy: 0.2016, loss: 3.5811 ||: 100%|█████████████████████████████████████████████| 100/100 [00:11<00:00,  8.95it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.2716, loss: 3.5930 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 47.18it/s]
accuracy: 0.2704, loss: 3.4810 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 31.45it/s]

  0%|                                                                                          | 0/100 [00:00<?, ?it/s]
accuracy: 0.2465, loss: 3.4433 ||:   1%|▍                                              | 1/100 [00:00<00:24,  4.02it/s]
accuracy: 0.2516, loss: 3.4781 ||:   2%|▉                                              | 2/100 [00:00<00:20,  4.83it/s]
accuracy: 0.2580, loss: 3.4884 ||:   4

accuracy: 0.3786, loss: 3.4838 ||:   3%|█▍                                             | 3/100 [00:00<00:19,  4.99it/s]
accuracy: 0.3761, loss: 3.3997 ||:   4%|█▉                                             | 4/100 [00:00<00:19,  4.81it/s]
accuracy: 0.3751, loss: 3.3371 ||:   6%|██▊                                            | 6/100 [00:00<00:15,  5.99it/s]
accuracy: 0.3726, loss: 3.2856 ||:   8%|███▊                                           | 8/100 [00:00<00:12,  7.08it/s]
accuracy: 0.3757, loss: 3.2559 ||:   9%|████▏                                          | 9/100 [00:01<00:12,  7.57it/s]
accuracy: 0.3770, loss: 3.2376 ||:  10%|████▌                                         | 10/100 [00:01<00:11,  8.10it/s]
accuracy: 0.3885, loss: 3.2143 ||:  11%|█████                                         | 11/100 [00:01<00:12,  7.22it/s]
accuracy: 0.3887, loss: 3.1970 ||:  13%|█████▉                                        | 13/100 [00:01<00:10,  8.20it/s]
accuracy: 0.3863, loss: 3.1925 ||:  14%|

...

accuracy: 0.9481, loss: 0.2631 ||:  55%|█████████████████████████▎                    | 55/100 [00:05<00:04, 10.04it/s]
accuracy: 0.9477, loss: 0.2673 ||:  57%|██████████████████████████▏                   | 57/100 [00:05<00:04, 10.27it/s]
accuracy: 0.9476, loss: 0.2717 ||:  59%|███████████████████████████▏                  | 59/100 [00:06<00:03, 11.49it/s]
accuracy: 0.9472, loss: 0.2759 ||:  61%|████████████████████████████                  | 61/100 [00:06<00:03, 11.07it/s]
accuracy: 0.9470, loss: 0.2755 ||:  63%|████████████████████████████▉                 | 63/100 [00:06<00:03,  9.81it/s]
accuracy: 0.9465, loss: 0.2754 ||:  65%|█████████████████████████████▉                | 65/100 [00:06<00:04,  7.89it/s]
accuracy: 0.9465, loss: 0.2744 ||:  67%|██████████████████████████████▊               | 67/100 [00:06<00:03,  8.88it/s]
accuracy: 0.9459, loss: 0.2798 ||:  70%|████████████████████████████████▏             | 70/100 [00:07<00:03,  9.15it/s]
accuracy: 0.9461, loss: 0.2790 ||:  71%|

accuracy: 0.9467, loss: 0.2704 ||:  87%|████████████████████████████████████████      | 87/100 [00:08<00:01, 10.39it/s]
accuracy: 0.9468, loss: 0.2698 ||:  89%|████████████████████████████████████████▉     | 89/100 [00:09<00:01, 10.31it/s]
accuracy: 0.9469, loss: 0.2689 ||:  91%|█████████████████████████████████████████▊    | 91/100 [00:09<00:00, 11.06it/s]
accuracy: 0.9468, loss: 0.2694 ||:  93%|██████████████████████████████████████████▊   | 93/100 [00:09<00:00, 12.44it/s]
accuracy: 0.9466, loss: 0.2694 ||:  95%|███████████████████████████████████████████▋  | 95/100 [00:09<00:00,  9.48it/s]
accuracy: 0.9469, loss: 0.2684 ||:  97%|████████████████████████████████████████████▌ | 97/100 [00:09<00:00,  9.76it/s]
accuracy: 0.9471, loss: 0.2667 ||: 100%|█████████████████████████████████████████████| 100/100 [00:10<00:00,  9.88it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.8600, loss: 0.7688 ||:  60%

accuracy: 0.9435, loss: 0.2654 ||:  11%|█████                                         | 11/100 [00:01<00:12,  7.08it/s]
accuracy: 0.9437, loss: 0.2686 ||:  13%|█████▉                                        | 13/100 [00:01<00:10,  8.01it/s]
accuracy: 0.9440, loss: 0.2686 ||:  14%|██████▍                                       | 14/100 [00:01<00:11,  7.64it/s]
accuracy: 0.9447, loss: 0.2656 ||:  16%|███████▎                                      | 16/100 [00:02<00:10,  8.07it/s]
accuracy: 0.9457, loss: 0.2575 ||:  18%|████████▎                                     | 18/100 [00:02<00:09,  9.06it/s]
accuracy: 0.9454, loss: 0.2714 ||:  20%|█████████▏                                    | 20/100 [00:02<00:08,  9.27it/s]
accuracy: 0.9461, loss: 0.2664 ||:  22%|██████████                                    | 22/100 [00:02<00:07,  9.87it/s]
accuracy: 0.9469, loss: 0.2614 ||:  24%|███████████                                   | 24/100 [00:02<00:08,  9.23it/s]
accuracy: 0.9475, loss: 0.2579 ||:  26%|

accuracy: 0.9492, loss: 0.2565 ||:  46%|█████████████████████▏                        | 46/100 [00:04<00:05,  9.13it/s]
accuracy: 0.9493, loss: 0.2558 ||:  48%|██████████████████████                        | 48/100 [00:04<00:05,  9.17it/s]
accuracy: 0.9491, loss: 0.2544 ||:  50%|███████████████████████                       | 50/100 [00:05<00:06,  7.83it/s]
accuracy: 0.9495, loss: 0.2518 ||:  52%|███████████████████████▉                      | 52/100 [00:05<00:05,  9.20it/s]
accuracy: 0.9494, loss: 0.2563 ||:  55%|█████████████████████████▎                    | 55/100 [00:05<00:04, 10.45it/s]
accuracy: 0.9488, loss: 0.2580 ||:  57%|██████████████████████████▏                   | 57/100 [00:05<00:04,  9.97it/s]
accuracy: 0.9488, loss: 0.2597 ||:  59%|███████████████████████████▏                  | 59/100 [00:05<00:03, 11.02it/s]
accuracy: 0.9490, loss: 0.2580 ||:  61%|████████████████████████████                  | 61/100 [00:06<00:03, 11.55it/s]
accuracy: 0.9484, loss: 0.2589 ||:  63%|

{'best_epoch': 276,
 'peak_cpu_memory_MB': 0,
 'training_duration': '0:52:11.995253',
 'training_start_epoch': 0,
 'training_epochs': 285,
 'epoch': 285,
 'training_accuracy': 0.9477160927617709,
 'training_loss': 0.26438863709568977,
 'training_cpu_memory_MB': 0.0,
 'validation_accuracy': 0.8658634538152611,
 'validation_loss': 0.6843086272478104,
 'best_validation_accuracy': 0.8658634538152611,
 'best_validation_loss': 0.6793955981731414}

Now do the same training (5K sentence training and 5K sentence validation sets) with GloVE embeddings:

In [29]:
glove_token_embedding_big = Embedding.from_params(vocab=vocab_big,
                            params=Params({'pretrained_file':'glove.6B.300d.txt',
                                           'embedding_dim' : EMBEDDING_DIM}))

glove_word_embeddings_big = BasicTextFieldEmbedder({"tokens": glove_token_embedding_big})
glove_model_big = LstmTagger(glove_word_embeddings_big, lstm, vocab_big)

trainer_glove_model_big=initialize_trainer(glove_model_big,vocab_big,train_dataset_big,validation_dataset_big,batch_size=50)
trainer_glove_model_big.train()


0it [00:00, ?it/s]
337it [00:00, 3337.16it/s]
1114it [00:00, 4026.22it/s]
1418it [00:00, 3342.63it/s]
2401it [00:00, 4162.68it/s]
3406it [00:00, 5042.74it/s]
4530it [00:00, 6032.59it/s]
5314it [00:00, 6432.90it/s]
6658it [00:00, 7613.10it/s]
8260it [00:00, 9020.29it/s]
9521it [00:01, 9840.28it/s]
11227it [00:01, 11249.29it/s]
13613it [00:01, 13347.03it/s]
15666it [00:01, 14880.29it/s]
17422it [00:01, 15190.26it/s]
19627it [00:01, 16716.41it/s]
21657it [00:01, 17606.05it/s]
23556it [00:01, 17124.01it/s]
26080it [00:01, 18910.28it/s]
30640it [00:01, 22903.92it/s]
35699it [00:02, 27358.61it/s]
40921it [00:02, 31859.51it/s]
45823it [00:02, 35522.80it/s]
50740it [00:02, 38659.83it/s]
55648it [00:02, 41289.55it/s]
60475it [00:02, 43044.63it/s]
65494it [00:02, 44850.59it/s]
70481it [00:02, 46122.70it/s]
75513it [00:02, 47175.52it/s]
80454it [00:02, 47688.08it/s]
85447it [00:03, 48199.36it/s]
90490it [00:03, 48710.79it/s]
95410it [00:03, 48853.56it/s]
100379it [00:03, 49101.50it/s]
105373it [

accuracy: 0.3179, loss: 3.6046 ||:  95%|███████████████████████████████████████████▋  | 95/100 [00:09<00:00, 12.10it/s]
accuracy: 0.3176, loss: 3.6035 ||:  97%|████████████████████████████████████████████▌ | 97/100 [00:09<00:00, 13.11it/s]
accuracy: 0.3184, loss: 3.5944 ||: 100%|█████████████████████████████████████████████| 100/100 [00:10<00:00,  9.87it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.3252, loss: 3.4687 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 48.79it/s]
accuracy: 0.3412, loss: 3.3702 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 35.22it/s]

  0%|                                                                                          | 0/100 [00:00<?, ?it/s]
accuracy: 0.3277, loss: 3.4564 ||:   1%|▍                                              | 1/100 [00:00<00:17,  5.68it/s]
accuracy: 0.3402, loss: 3.3693 ||:   2

accuracy: 0.3737, loss: 2.9955 ||:  14%|██████▍                                       | 14/100 [00:01<00:09,  8.70it/s]
accuracy: 0.3712, loss: 3.0928 ||:  16%|███████▎                                      | 16/100 [00:01<00:08, 10.11it/s]
accuracy: 0.3703, loss: 3.0703 ||:  18%|████████▎                                     | 18/100 [00:01<00:07, 10.41it/s]
accuracy: 0.3718, loss: 3.0426 ||:  20%|█████████▏                                    | 20/100 [00:02<00:07, 10.33it/s]
accuracy: 0.3783, loss: 3.0156 ||:  22%|██████████                                    | 22/100 [00:02<00:13,  5.98it/s]
accuracy: 0.3795, loss: 3.0018 ||:  23%|██████████▌                                   | 23/100 [00:02<00:11,  6.67it/s]
accuracy: 0.3784, loss: 2.9991 ||:  25%|███████████▌                                  | 25/100 [00:02<00:09,  7.91it/s]
accuracy: 0.3796, loss: 2.9767 ||:  27%|████████████▍                                 | 27/100 [00:03<00:08,  8.72it/s]
accuracy: 0.3786, loss: 2.9672 ||:  29%|

accuracy: 0.4278, loss: 2.5997 ||:  47%|█████████████████████▌                        | 47/100 [00:05<00:05,  9.27it/s]
accuracy: 0.4273, loss: 2.5964 ||:  49%|██████████████████████▌                       | 49/100 [00:05<00:05,  9.79it/s]
accuracy: 0.4269, loss: 2.5904 ||:  51%|███████████████████████▍                      | 51/100 [00:05<00:05,  9.42it/s]
accuracy: 0.4274, loss: 2.5827 ||:  53%|████████████████████████▍                     | 53/100 [00:06<00:04, 10.68it/s]
accuracy: 0.4264, loss: 2.6017 ||:  56%|█████████████████████████▊                    | 56/100 [00:06<00:03, 11.55it/s]
accuracy: 0.4264, loss: 2.5945 ||:  58%|██████████████████████████▋                   | 58/100 [00:06<00:03, 11.09it/s]
accuracy: 0.4273, loss: 2.5886 ||:  60%|███████████████████████████▌                  | 60/100 [00:06<00:03, 10.66it/s]
accuracy: 0.4281, loss: 2.6055 ||:  62%|████████████████████████████▌                 | 62/100 [00:06<00:03,  9.78it/s]
accuracy: 0.4283, loss: 2.6005 ||:  64%|

accuracy: 0.4582, loss: 2.4477 ||:  84%|██████████████████████████████████████▋       | 84/100 [00:08<00:01, 12.77it/s]
accuracy: 0.4585, loss: 2.4429 ||:  86%|███████████████████████████████████████▌      | 86/100 [00:08<00:01, 12.31it/s]
accuracy: 0.4582, loss: 2.4441 ||:  88%|████████████████████████████████████████▍     | 88/100 [00:08<00:00, 12.01it/s]
accuracy: 0.4584, loss: 2.4390 ||:  90%|█████████████████████████████████████████▍    | 90/100 [00:09<00:00, 10.41it/s]
accuracy: 0.4591, loss: 2.4333 ||:  92%|██████████████████████████████████████████▎   | 92/100 [00:09<00:00, 10.14it/s]
accuracy: 0.4597, loss: 2.4270 ||:  94%|███████████████████████████████████████████▏  | 94/100 [00:09<00:00, 10.04it/s]
accuracy: 0.4601, loss: 2.4248 ||:  96%|████████████████████████████████████████████▏ | 96/100 [00:09<00:00,  9.31it/s]
accuracy: 0.4603, loss: 2.4233 ||:  97%|████████████████████████████████████████████▌ | 97/100 [00:10<00:00,  7.58it/s]
accuracy: 0.4605, loss: 2.4194 ||: 100%|

...

accuracy: 0.8872, loss: 0.4532 ||:  89%|████████████████████████████████████████▉     | 89/100 [00:09<00:01,  8.34it/s]
accuracy: 0.8872, loss: 0.4531 ||:  91%|█████████████████████████████████████████▊    | 91/100 [00:09<00:01,  8.15it/s]
accuracy: 0.8874, loss: 0.4525 ||:  92%|██████████████████████████████████████████▎   | 92/100 [00:09<00:00,  8.52it/s]
accuracy: 0.8870, loss: 0.4534 ||:  94%|███████████████████████████████████████████▏  | 94/100 [00:10<00:00,  8.80it/s]
accuracy: 0.8867, loss: 0.4546 ||:  95%|███████████████████████████████████████████▋  | 95/100 [00:10<00:00,  8.37it/s]
accuracy: 0.8870, loss: 0.4528 ||:  97%|████████████████████████████████████████████▌ | 97/100 [00:10<00:00,  9.27it/s]
accuracy: 0.8866, loss: 0.4540 ||:  99%|█████████████████████████████████████████████▌| 99/100 [00:10<00:00,  9.17it/s]
accuracy: 0.8862, loss: 0.4552 ||: 100%|█████████████████████████████████████████████| 100/100 [00:10<00:00,  9.29it/s]

  0%|                                  

accuracy: 0.8592, loss: 0.7508 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 47.63it/s]
accuracy: 0.8598, loss: 0.6693 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 34.02it/s]

  0%|                                                                                          | 0/100 [00:00<?, ?it/s]
accuracy: 0.8809, loss: 0.5033 ||:   1%|▍                                              | 1/100 [00:00<00:37,  2.67it/s]
accuracy: 0.8881, loss: 0.4720 ||:   3%|█▍                                             | 3/100 [00:00<00:28,  3.41it/s]
accuracy: 0.8868, loss: 0.5112 ||:   5%|██▎                                            | 5/100 [00:00<00:21,  4.39it/s]
accuracy: 0.8866, loss: 0.4846 ||:   7%|███▎                                           | 7/100 [00:00<00:17,  5.29it/s]
accuracy: 0.8885, loss: 0.4717 ||:   9%|████▏                                          | 9/100 [00:01<00:14,  6.39it/s]
accuracy: 0.8868, loss: 0.4721 ||:  10%

accuracy: 0.8931, loss: 0.4140 ||:  11%|█████                                         | 11/100 [00:01<00:11,  7.74it/s]
accuracy: 0.8930, loss: 0.4124 ||:  12%|█████▌                                        | 12/100 [00:01<00:10,  8.16it/s]
accuracy: 0.8929, loss: 0.4149 ||:  13%|█████▉                                        | 13/100 [00:01<00:10,  8.40it/s]
accuracy: 0.8910, loss: 0.4198 ||:  14%|██████▍                                       | 14/100 [00:01<00:11,  7.49it/s]
accuracy: 0.8908, loss: 0.4182 ||:  15%|██████▉                                       | 15/100 [00:01<00:10,  7.75it/s]
accuracy: 0.8898, loss: 0.4211 ||:  16%|███████▎                                      | 16/100 [00:02<00:10,  7.93it/s]
accuracy: 0.8905, loss: 0.4211 ||:  18%|████████▎                                     | 18/100 [00:02<00:09,  8.37it/s]
accuracy: 0.8878, loss: 0.4241 ||:  19%|████████▋                                     | 19/100 [00:02<00:22,  3.63it/s]
accuracy: 0.8877, loss: 0.4448 ||:  21%|

accuracy: 0.8870, loss: 0.4354 ||:  23%|██████████▌                                   | 23/100 [00:02<00:08,  8.66it/s]
accuracy: 0.8878, loss: 0.4317 ||:  25%|███████████▌                                  | 25/100 [00:03<00:08,  9.32it/s]
accuracy: 0.8880, loss: 0.4290 ||:  27%|████████████▍                                 | 27/100 [00:03<00:07,  9.89it/s]
accuracy: 0.8873, loss: 0.4305 ||:  29%|█████████████▎                                | 29/100 [00:03<00:07,  9.21it/s]
accuracy: 0.8855, loss: 0.4399 ||:  31%|██████████████▎                               | 31/100 [00:03<00:07,  8.92it/s]
accuracy: 0.8854, loss: 0.4448 ||:  33%|███████████████▏                              | 33/100 [00:03<00:06, 10.02it/s]
accuracy: 0.8858, loss: 0.4445 ||:  35%|████████████████                              | 35/100 [00:04<00:06, 10.26it/s]
accuracy: 0.8858, loss: 0.4455 ||:  37%|█████████████████                             | 37/100 [00:04<00:06,  9.39it/s]
accuracy: 0.8858, loss: 0.4476 ||:  39%|

{'best_epoch': 274,
 'peak_cpu_memory_MB': 0,
 'training_duration': '0:51:05.437057',
 'training_start_epoch': 0,
 'training_epochs': 283,
 'epoch': 283,
 'training_accuracy': 0.8877522337114747,
 'training_loss': 0.44782074958086016,
 'training_cpu_memory_MB': 0.0,
 'validation_accuracy': 0.8606425702811245,
 'validation_loss': 0.6671894907951355,
 'best_validation_accuracy': 0.8585341365461847,
 'best_validation_loss': 0.66714628636837}

For each trained model, record validation accuracy and training duration (they are returned along with other training stats after training a model) and accuracy on the test set. Fill in the numbers in the table below:

| model | validation accuracy | training accuracy | training duration|
|-------|---------------------|---------------|-------------------------------------------
| basic model on 50 sentences|0.40217391304347827|0.4213006597549482|0:03:52.203449|
| glove model on 50 sentences|0.5355731225296443|0.6503298774740811|0:03:30.964794|
| basic model on 500 sentences|0.6997991967871486|0.8920169687620517|0:21:10.950190|
| glove model on 500 sentences|0.772289156626506|0.8928846895487852|0:23:07.505913|
| basic model on 5000 sentences|0.8658634538152611|0.9477160927617709|0:52:11.995253|
| glove model on 5000 sentences|0.8606425702811245| 0.8877522337114747|0:51:05.437057|

**Question.** What do you conclude from these comparisons? when can it be especially beneficial to initialize a model with pretrained embeddings?

**Answer.** By looking at the comparisons we could observe that, while on the smaller number of sentences the pre-trained embeddings provide a far better model, as the number of sentences grows the benefit of the pre-trained model is getting smaller and when using the 5k sentences the pre-trained model is worse. So it is very benefitial to initialize a model with pretrained embeddings on cases where the training set is small, but in cases where the training set is sufficient there is no need for the pretrained embeddings, because they could also affect the model negatively.

During training, data is processed in batches so that the model performs computation for multiple examples simultaneously. How does batching affect model training? Modify the training to have smaller batches of data - let's use batches of 5 or 500 instead of 50. How does this affect the results? 

In [30]:
#Define your trainers with alternative batching here: batches of 5, 50 sentences
basic_trainer_tinySP1=initialize_trainer(model_tiny,vocab_tiny,train_dataset_tiny,validation_dataset_tiny,batch_size=5)
basic_trainer_tinySP1.train()


  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.4151, loss: 2.6643 ||:  10%|████▊                                           | 1/10 [00:00<00:01,  5.26it/s]
accuracy: 0.3908, loss: 2.9112 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00,  7.08it/s]
accuracy: 0.4194, loss: 2.8711 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 19.84it/s]

accuracy: 0.4022, loss: 2.9139 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 166.70it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.4528, loss: 2.7032 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:00, 35.72it/s]
accuracy: 0.4298, loss: 2.8101 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 31.45it/s]

accuracy: 0.4160, loss: 2.8845 ||: 1

accuracy: 0.4994, loss: 2.3331 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 19.06it/s]
accuracy: 0.4854, loss: 2.3418 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 20.92it/s]

accuracy: 0.4644, loss: 2.5582 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 104.18it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.4957, loss: 2.2310 ||:  20%|█████████▌                                      | 2/10 [00:00<00:00, 14.86it/s]
accuracy: 0.5348, loss: 2.1101 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:00, 14.91it/s]
accuracy: 0.4901, loss: 2.3311 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 23.44it/s]

accuracy: 0.4615, loss: 2.5521 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 137.01it/s]

  0%|                               

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.5448, loss: 1.9771 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 39.22it/s]

accuracy: 0.4713, loss: 2.4024 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 140.86it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.5378, loss: 2.0509 ||:  30%|██████████████▍                                 | 3/10 [00:00<00:00, 26.55it/s]
accuracy: 0.5504, loss: 1.9664 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 38.32it/s]

accuracy: 0.4654, loss: 2.3983 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 161.32it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.5419, loss: 1.9740 ||:  

accuracy: 0.6664, loss: 1.6160 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 37.88it/s]

accuracy: 0.4891, loss: 2.2959 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 196.11it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.6659, loss: 1.6765 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 40.99it/s]
accuracy: 0.6664, loss: 1.6056 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 37.60it/s]

accuracy: 0.4901, loss: 2.2941 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 161.32it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.6748, loss: 1.5950 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 48.32it/s]

accuracy: 0.4921, loss: 2.2898 ||: 

accuracy: 0.7587, loss: 1.3045 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 21.97it/s]

accuracy: 0.5079, loss: 2.2209 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 185.21it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.7778, loss: 1.2389 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 43.48it/s]
accuracy: 0.7587, loss: 1.2957 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 37.74it/s]

accuracy: 0.5079, loss: 2.2223 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 144.95it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.7629, loss: 1.3915 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:00, 29.63it/s]
accuracy: 0.7625, loss: 1.2871 ||: 1

accuracy: 0.8190, loss: 1.0468 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 40.01it/s]

accuracy: 0.5356, loss: 2.1673 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 146.80it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.8084, loss: 1.0118 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 42.86it/s]
accuracy: 0.8200, loss: 1.0397 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 38.77it/s]

accuracy: 0.5385, loss: 2.1671 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 161.32it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.8508, loss: 0.9244 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 47.63it/s]
accuracy: 0.8209, loss: 1.0331 ||: 1

accuracy: 0.5593, loss: 2.1355 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 161.32it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.8575, loss: 0.9044 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:00, 39.22it/s]
accuracy: 0.8577, loss: 0.8399 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 38.92it/s]

accuracy: 0.5583, loss: 2.1358 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 161.32it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.8397, loss: 0.9051 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 40.01it/s]
accuracy: 0.8577, loss: 0.8347 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 39.07it/s]

accuracy: 0.5593, loss: 2.1373 ||: 1

accuracy: 0.5741, loss: 2.1220 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 138.91it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.8813, loss: 0.6642 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 48.08it/s]
accuracy: 0.8841, loss: 0.6902 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 40.17it/s]

accuracy: 0.5731, loss: 2.1232 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 181.85it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.8893, loss: 0.6638 ||:  60%|████████████████████████████▊                   | 6/10 [00:00<00:00, 45.46it/s]
accuracy: 0.8841, loss: 0.6863 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 38.92it/s]

accuracy: 0.5761, loss: 2.1234 ||: 1

accuracy: 0.5909, loss: 2.1214 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 172.44it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.9040, loss: 0.6604 ||:  40%|███████████████████▏                            | 4/10 [00:00<00:00, 38.84it/s]
accuracy: 0.9086, loss: 0.5789 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 38.92it/s]

accuracy: 0.5909, loss: 2.1214 ||: 100%|██████████████████████████████████████████████| 10/10 [00:00<00:00, 163.96it/s]

  0%|                                                                                           | 0/10 [00:00<?, ?it/s]
accuracy: 0.9093, loss: 0.5484 ||:  50%|████████████████████████                        | 5/10 [00:00<00:00, 47.18it/s]
accuracy: 0.9076, loss: 0.5761 ||: 100%|███████████████████████████████████████████████| 10/10 [00:00<00:00, 39.07it/s]

accuracy: 0.5909, loss: 2.1221 ||: 1

{'best_epoch': 256,
 'peak_cpu_memory_MB': 0,
 'training_duration': '0:01:33.330317',
 'training_start_epoch': 0,
 'training_epochs': 265,
 'epoch': 265,
 'training_accuracy': 0.9076343072573044,
 'training_loss': 0.5760573625564576,
 'training_cpu_memory_MB': 0.0,
 'validation_accuracy': 0.5909090909090909,
 'validation_loss': 2.122134804725647,
 'best_validation_accuracy': 0.5889328063241107,
 'best_validation_loss': 2.11926292181015}

In [31]:
# batches of 5, 500 sentences
basic_trainer_regularSP1=initialize_trainer(model_regular,vocab_regular,train_dataset_regular,validation_dataset_regular,batch_size=5)
basic_trainer_regularSP1.train()


  0%|                                                                                          | 0/100 [00:00<?, ?it/s]
accuracy: 0.5155, loss: 2.5715 ||:   3%|█▍                                             | 3/100 [00:00<00:05, 19.11it/s]
accuracy: 0.5797, loss: 2.0060 ||:   6%|██▊                                            | 6/100 [00:00<00:04, 20.57it/s]
accuracy: 0.6089, loss: 1.7547 ||:   9%|████▏                                          | 9/100 [00:00<00:04, 22.66it/s]
accuracy: 0.6311, loss: 1.6106 ||:  13%|█████▉                                        | 13/100 [00:00<00:03, 25.07it/s]
accuracy: 0.6495, loss: 1.4881 ||:  17%|███████▊                                      | 17/100 [00:00<00:03, 25.72it/s]
accuracy: 0.6546, loss: 1.5191 ||:  20%|█████████▏                                    | 20/100 [00:00<00:03, 25.31it/s]
accuracy: 0.6708, loss: 1.4075 ||:  24%|███████████                                   | 24/100 [00:00<00:02, 28.38it/s]
accuracy: 0.6880, loss: 1.3751 ||:  28%

accuracy: 0.7011, loss: 1.3518 ||: 100%|████████████████████████████████████████████| 100/100 [00:00<00:00, 195.34it/s]

  0%|                                                                                          | 0/100 [00:00<?, ?it/s]
accuracy: 0.8739, loss: 0.6311 ||:   4%|█▉                                             | 4/100 [00:00<00:03, 30.54it/s]
accuracy: 0.8866, loss: 0.5800 ||:   8%|███▊                                           | 8/100 [00:00<00:02, 32.16it/s]
accuracy: 0.8909, loss: 0.5447 ||:  12%|█████▌                                        | 12/100 [00:00<00:02, 32.99it/s]
accuracy: 0.8913, loss: 0.5485 ||:  17%|███████▊                                      | 17/100 [00:00<00:02, 35.49it/s]
accuracy: 0.8939, loss: 0.5484 ||:  20%|█████████▏                                    | 20/100 [00:00<00:02, 30.75it/s]
accuracy: 0.8908, loss: 0.5775 ||:  24%|███████████                                   | 24/100 [00:00<00:02, 30.68it/s]
accuracy: 0.8900, loss: 0.5834 ||:  28%

accuracy: 0.7009, loss: 1.4025 ||:  69%|███████████████████████████████              | 69/100 [00:00<00:00, 228.30it/s]
accuracy: 0.7044, loss: 1.3361 ||: 100%|████████████████████████████████████████████| 100/100 [00:00<00:00, 202.52it/s]

  0%|                                                                                          | 0/100 [00:00<?, ?it/s]
accuracy: 0.8961, loss: 0.5326 ||:   3%|█▍                                             | 3/100 [00:00<00:03, 26.79it/s]
accuracy: 0.8961, loss: 0.6306 ||:   6%|██▊                                            | 6/100 [00:00<00:03, 26.79it/s]
accuracy: 0.9031, loss: 0.5549 ||:  10%|████▌                                         | 10/100 [00:00<00:03, 29.15it/s]
accuracy: 0.8951, loss: 0.5353 ||:  13%|█████▉                                        | 13/100 [00:00<00:03, 25.12it/s]
accuracy: 0.8986, loss: 0.5079 ||:  16%|███████▎                                      | 16/100 [00:00<00:03, 25.54it/s]
accuracy: 0.8909, loss: 0.5928 ||:  20%

  0%|                                                                                          | 0/100 [00:00<?, ?it/s]
accuracy: 0.8971, loss: 0.5240 ||:   4%|█▉                                             | 4/100 [00:00<00:03, 28.37it/s]
accuracy: 0.9145, loss: 0.4251 ||:   8%|███▊                                           | 8/100 [00:00<00:03, 29.97it/s]
accuracy: 0.9017, loss: 0.4678 ||:  11%|█████                                         | 11/100 [00:00<00:03, 26.84it/s]
accuracy: 0.8999, loss: 0.5235 ||:  15%|██████▉                                       | 15/100 [00:00<00:03, 27.39it/s]
accuracy: 0.9039, loss: 0.4946 ||:  18%|████████▎                                     | 18/100 [00:00<00:02, 27.51it/s]
accuracy: 0.9034, loss: 0.4966 ||:  21%|█████████▋                                    | 21/100 [00:00<00:03, 25.88it/s]
accuracy: 0.9053, loss: 0.4871 ||:  25%|███████████▌                                  | 25/100 [00:00<00:02, 27.23it/s]
accuracy: 0.9051, loss: 0.4879 ||:  29%|

accuracy: 0.9275, loss: 0.4134 ||:   7%|███▎                                           | 7/100 [00:00<00:03, 27.22it/s]
accuracy: 0.9009, loss: 0.4811 ||:  11%|█████                                         | 11/100 [00:00<00:03, 28.74it/s]
accuracy: 0.9052, loss: 0.4744 ||:  14%|██████▍                                       | 14/100 [00:00<00:03, 27.74it/s]
accuracy: 0.9083, loss: 0.4749 ||:  17%|███████▊                                      | 17/100 [00:00<00:03, 26.64it/s]
accuracy: 0.9106, loss: 0.4512 ||:  20%|█████████▏                                    | 20/100 [00:00<00:02, 27.34it/s]
accuracy: 0.9066, loss: 0.4683 ||:  23%|██████████▌                                   | 23/100 [00:00<00:02, 26.88it/s]
accuracy: 0.9041, loss: 0.4743 ||:  27%|████████████▍                                 | 27/100 [00:00<00:02, 28.48it/s]
accuracy: 0.9056, loss: 0.4914 ||:  31%|██████████████▎                               | 31/100 [00:01<00:02, 30.81it/s]
accuracy: 0.9054, loss: 0.5011 ||:  35%|

...

accuracy: 0.9275, loss: 0.4243 ||:  65%|█████████████████████████████▉                | 65/100 [00:02<00:01, 31.60it/s]
accuracy: 0.9280, loss: 0.4228 ||:  69%|███████████████████████████████▋              | 69/100 [00:02<00:00, 31.13it/s]
accuracy: 0.9253, loss: 0.4258 ||:  73%|█████████████████████████████████▌            | 73/100 [00:02<00:00, 29.84it/s]
accuracy: 0.9252, loss: 0.4284 ||:  78%|███████████████████████████████████▉          | 78/100 [00:02<00:00, 32.88it/s]
accuracy: 0.9252, loss: 0.4294 ||:  82%|█████████████████████████████████████▋        | 82/100 [00:02<00:00, 32.37it/s]
accuracy: 0.9229, loss: 0.4331 ||:  86%|███████████████████████████████████████▌      | 86/100 [00:02<00:00, 30.92it/s]
accuracy: 0.9233, loss: 0.4312 ||:  90%|█████████████████████████████████████████▍    | 90/100 [00:02<00:00, 29.90it/s]
accuracy: 0.9233, loss: 0.4310 ||:  94%|███████████████████████████████████████████▏  | 94/100 [00:02<00:00, 30.37it/s]
accuracy: 0.9231, loss: 0.4319 ||: 100%|

accuracy: 0.7338, loss: 1.4535 ||:  47%|█████████████████████▏                       | 47/100 [00:00<00:00, 232.30it/s]
accuracy: 0.7172, loss: 1.3802 ||:  72%|████████████████████████████████▍            | 72/100 [00:00<00:00, 236.01it/s]
accuracy: 0.7224, loss: 1.3151 ||: 100%|████████████████████████████████████████████| 100/100 [00:00<00:00, 214.17it/s]

  0%|                                                                                          | 0/100 [00:00<?, ?it/s]
accuracy: 0.9254, loss: 0.3985 ||:   2%|▉                                              | 2/100 [00:00<00:05, 18.87it/s]
accuracy: 0.9389, loss: 0.3300 ||:   6%|██▊                                            | 6/100 [00:00<00:04, 22.02it/s]
accuracy: 0.9344, loss: 0.3642 ||:  10%|████▌                                         | 10/100 [00:00<00:03, 25.02it/s]
accuracy: 0.9394, loss: 0.3723 ||:  14%|██████▍                                       | 14/100 [00:00<00:03, 28.07it/s]
accuracy: 0.9407, loss: 0.3689 ||:  17%

accuracy: 0.9254, loss: 0.5738 ||:   6%|██▊                                            | 6/100 [00:00<00:03, 27.06it/s]
accuracy: 0.9285, loss: 0.4835 ||:  10%|████▌                                         | 10/100 [00:00<00:03, 28.01it/s]
accuracy: 0.9361, loss: 0.4340 ||:  14%|██████▍                                       | 14/100 [00:00<00:03, 28.06it/s]
accuracy: 0.9367, loss: 0.4149 ||:  17%|███████▊                                      | 17/100 [00:00<00:03, 27.00it/s]
accuracy: 0.9370, loss: 0.4111 ||:  20%|█████████▏                                    | 20/100 [00:00<00:02, 27.76it/s]
accuracy: 0.9369, loss: 0.4113 ||:  24%|███████████                                   | 24/100 [00:00<00:02, 29.61it/s]
accuracy: 0.9381, loss: 0.3986 ||:  29%|█████████████▎                                | 29/100 [00:00<00:02, 31.39it/s]
accuracy: 0.9352, loss: 0.3986 ||:  33%|███████████████▏                              | 33/100 [00:01<00:02, 26.97it/s]
accuracy: 0.9306, loss: 0.4136 ||:  36%|

accuracy: 0.9468, loss: 0.3135 ||:  27%|████████████▍                                 | 27/100 [00:00<00:02, 32.56it/s]
accuracy: 0.9427, loss: 0.3492 ||:  31%|██████████████▎                               | 31/100 [00:00<00:02, 31.40it/s]
accuracy: 0.9408, loss: 0.3496 ||:  35%|████████████████                              | 35/100 [00:01<00:02, 30.78it/s]
accuracy: 0.9415, loss: 0.3434 ||:  39%|█████████████████▉                            | 39/100 [00:01<00:02, 29.23it/s]
accuracy: 0.9420, loss: 0.3429 ||:  42%|███████████████████▎                          | 42/100 [00:01<00:01, 29.20it/s]
accuracy: 0.9395, loss: 0.3573 ||:  46%|█████████████████████▏                        | 46/100 [00:01<00:01, 30.61it/s]
accuracy: 0.9404, loss: 0.3539 ||:  50%|███████████████████████                       | 50/100 [00:01<00:01, 32.29it/s]
accuracy: 0.9402, loss: 0.3549 ||:  54%|████████████████████████▊                     | 54/100 [00:01<00:01, 33.08it/s]
accuracy: 0.9401, loss: 0.3599 ||:  58%|

{'best_epoch': 29,
 'peak_cpu_memory_MB': 0,
 'training_duration': '0:02:28.005983',
 'training_start_epoch': 0,
 'training_epochs': 38,
 'epoch': 38,
 'training_accuracy': 0.940416505977632,
 'training_loss': 0.3651048780605197,
 'training_cpu_memory_MB': 0.0,
 'validation_accuracy': 0.731425702811245,
 'validation_loss': 1.3089696699380875,
 'best_validation_accuracy': 0.7255020080321285,
 'best_validation_loss': 1.3055689173936844}

In [32]:
#batches of 500, 50 sentences
basic_trainer_tinySP2=initialize_trainer(model_tiny,vocab_tiny,train_dataset_tiny,validation_dataset_tiny,batch_size=500)
basic_trainer_tinySP2.train()


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]
accuracy: 0.9105, loss: 0.5700 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.67it/s]

accuracy: 0.5899, loss: 2.1215 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 21.74it/s]

  0%|                                                                                            | 0/1 [00:00<?, ?it/s]
accuracy: 0.9105, loss: 0.5697 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.21it/s]

accuracy: 0.5899, loss: 2.1215 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.87it/s]

  0%|                                                                                            | 0/1 [00:00<?, ?it/s]
accuracy: 0.9105, loss: 0.5694 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.21it/s]

accuracy: 0.5909, loss: 2.1215 ||:

{'best_epoch': 1,
 'peak_cpu_memory_MB': 0,
 'training_duration': '0:00:02.551599',
 'training_start_epoch': 0,
 'training_epochs': 10,
 'epoch': 10,
 'training_accuracy': 0.9104618284637135,
 'training_loss': 0.5671795606613159,
 'training_cpu_memory_MB': 0.0,
 'validation_accuracy': 0.591897233201581,
 'validation_loss': 2.1218090057373047,
 'best_validation_accuracy': 0.5899209486166008,
 'best_validation_loss': 2.121480941772461}

In [33]:
#batches of 500, 500 sentences
basic_trainer_regularSP2=initialize_trainer(model_regular,vocab_regular,train_dataset_regular,validation_dataset_regular,batch_size=500)
basic_trainer_regularSP2.train()


  0%|                                                                                            | 0/1 [00:00<?, ?it/s]
accuracy: 0.9438, loss: 0.3547 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:01<00:00,  1.79s/it]

  0%|                                                                                            | 0/1 [00:00<?, ?it/s]
accuracy: 0.7277, loss: 1.3064 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  1.80it/s]

  0%|                                                                                            | 0/1 [00:00<?, ?it/s]
accuracy: 0.9437, loss: 0.3546 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:01<00:00,  1.74s/it]

  0%|                                                                                            | 0/1 [00:00<?, ?it/s]
accuracy: 0.7286, loss: 1.3064 ||: 100%|█████████████████████████████████████████████████| 1/1 [00:00<00:00,  1.83it/s]

  0%|                              

{'best_epoch': 1,
 'peak_cpu_memory_MB': 0,
 'training_duration': '0:00:25.442944',
 'training_start_epoch': 0,
 'training_epochs': 10,
 'epoch': 10,
 'training_accuracy': 0.9447551099112996,
 'training_loss': 0.3536790907382965,
 'training_cpu_memory_MB': 0.0,
 'validation_accuracy': 0.7299196787148594,
 'validation_loss': 1.307321548461914,
 'best_validation_accuracy': 0.7286144578313253,
 'best_validation_loss': 1.3063677549362183}

Report your results below:

**batches of 5**:

| model | validation accuracy | training accuracy | training duration|
|-------|---------------------|---------------|-------------------------------------------
| basic model on 50 sentences|0.5909090909090909|0.9076343072573044|0:01:33.330317|
| basic model on 500 sentences|0.731425702811245|0.940416505977632|0:02:28.005983|

**batches of 500**:

| model | validation accuracy | training accuracy | training duration|
|-------|---------------------|---------------|-------------------------------------------
| basic model on 50 sentences|0.591897233201581|0.9104618284637135|0:00:02.551599|
| basic model on 500 sentences|0.7299196787148594|0.9447551099112996|0:00:25.442944|

**Question.** What do these results tell you?
**Answer.** The number of batches, as the duration results show, play a big role on the duration of the training and in the models here it doesn't affect the accuracy on both the training and the test set.

## Comment 
In this lab we used pretrained GloVe embeddings in a model for part of speech tagging. GloVe in its turn is also a neural word embedding model, but it had been trained on a completely different objective. GloVe vectors had been optimised on word cooccurrence matrix decomposition, i.e. on the task of predicting which words tend to occur with which other words. Part of speech certainly plays a role in determining statistical cooccurrence of words, but this role is indirect, and explicit part of speech information has not been used in training GloVe.

This makes our application an example of **transfer learning**, whereby a learned model trained on one objective (e.g. word cooccurrence) can benefit a different application (e.g. POS tagging), because some information is shared between them. 

END OF PART 1 of LAB 4 - to be updated next week 